### **Data Preprocessing**


In [1]:
%%capture
!pip install datasets
!pip install transformers
!pip install starcc
!pip install sacrebleu

In [1]:
from collections import defaultdict
from random import randint, choice
import math

typo_table = defaultdict(list)

with open("typos.txt", "r") as typos_file:
    for line in typos_file.read().splitlines():
        [correct, typo] = line.split("\t")
        typo_table[correct].append(typo)

def insert_typos(s: str) -> str:
    max_num_typos = randint(1, max(math.ceil(len(s) * 0.05), 1))
    num_typos = 0
    corrects = list(typo_table.keys())
    while num_typos < max_num_typos and len(corrects) > 0:
        correct = choice(corrects)
        corrects.remove(correct)
        typo = choice(typo_table[correct])
        if s.count(correct) > 0:
            num_typos += 1
        s = s.replace(correct, typo)
    return s

insert_typos("唔該你細聲啲，我喺度做緊嘢，使唔使講呢啲嘢。")

'唔該你細聲d，我喺度做緊嘢，洗唔洗講呢d嘢。'

In [2]:
import json
from StarCC import PresetConversion
convert = PresetConversion(src='cn', dst='hk', with_phrase=False)

with open("train/botisan.json", "r") as botisan_file, open("train/tatoeba.tsv", "r") as tatoeba_file, open("train/train.can", "w+") as can_file, open("train/train.man", "w+") as man_file:
    for line in botisan_file.readlines():
        translation = json.loads(line)["translation"]
        can_file.write(translation["yue"] + "\n")
        man_file.write(convert(translation["zh"]) + "\n")
        can_file.write(insert_typos(translation["yue"]) + "\n")
        man_file.write(convert(translation["zh"]) + "\n")
    
    for line in tatoeba_file.read().splitlines():
        [_, can, _, man] = line.split("\t")
        can_file.write(can + "\n")
        man_file.write(convert(man) + "\n")
        can_file.write(insert_typos(can) + "\n")
        man_file.write(convert(man) + "\n")


Building prefix dict from the default dictionary ...
Loading model from cache /var/folders/kk/n4ff6h1n3t170b1m4zv09yf40000gn/T/jieba.cache
Loading model cost 0.339 seconds.
Prefix dict has been built successfully.


In [3]:
from os import listdir
from os.path import isfile, join
man_dir = "train/man/"
can_dir = "train/can/"
man_paths = [f for f in listdir(man_dir) if isfile(join(man_dir, f)) and f != ".DS_Store"]
with open("train/train.can", "a+") as can_train_file, open("train/train.man", "a+") as man_train_file:
    for man_path in man_paths:
        with open(man_dir + man_path, "r") as man_file:
            name = man_path[len("man-"):-len(".txt")]
            can_path = "can-" + name + ".txt"
            with open(can_dir + can_path, "r") as can_file:
                for man_line, can_line in zip(man_file.readlines(), can_file.readlines()):
                    can_train_file.write(can_line.replace(" ", ""))
                    man_train_file.write(man_line.replace(" ", ""))
                    if name == "novels":
                        can_train_file.write(insert_typos(can_line.replace(" ", "")))
                        man_train_file.write(insert_typos(man_line.replace(" ", "")))

In [4]:
from datasets import Dataset

train_data = None
val_data = None
test_data = None

with open("train/train.can", "r") as can_file, open("train/train.man", "r") as man_file:
    train_data = Dataset.from_dict({"can": can_file.read().splitlines(), "man": man_file.read().splitlines()}).shuffle(seed=42).flatten_indices()
    print(f"Loaded training data.")
    print(f"First line: {train_data[0]}")

with open("para/dev/dev.can", "r") as can_file, open("para/dev/dev.man", "r") as man_file:
    val_data = Dataset.from_dict({"can": can_file.read().splitlines(), "man": man_file.read().splitlines()})
    print(f"Loaded validation data.")
    print(f"First line: {val_data[0]}")

with open("para/test/test.can", "r") as can_file, open("para/test/test.man", "r") as man_file:
    test_data = Dataset.from_dict({"can": can_file.read().splitlines(), "man": man_file.read().splitlines()})
    print(f"Loaded test data.")
    print(f"First line: {test_data[0]}")


Flattening the indices:   0%|          | 0/135792 [00:00<?, ? examples/s]

Loaded training data.
First line: {'can': '高溫、出汗及疲乏均會增加身體的負荷', 'man': '高温、出汗及疲乏均會增加身體的負荷'}
Loaded validation data.
First line: {'can': '啲咁耐就攪掂嘞，真係掯', 'man': '他一會兒工夫就弄好了，真神'}
Loaded test data.
First line: {'can': '筷子放喺你嘅右便', 'man': '筷子放在你的右邊'}


In [5]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('Ayaka/bart-base-cantonese')
tokenizer.bos_token = tokenizer.cls_token
tokenizer.eos_token = tokenizer.sep_token

In [6]:
batch_size=32  # change to 16 for full training
encoder_max_length=128
decoder_max_length=128

def process_data_to_model_inputs(batch):
  # tokenize the inputs and labels
  inputs = tokenizer(batch["can"], padding="max_length", truncation=True, max_length=encoder_max_length)
  outputs = tokenizer(batch["man"], padding="max_length", truncation=True, max_length=decoder_max_length)

  batch["input_ids"] = inputs.input_ids
#   batch["attention_mask"] = inputs.attention_mask
#   batch["decoder_input_ids"] = outputs.input_ids
#   batch["decoder_attention_mask"] = outputs.attention_mask
  batch["labels"] = outputs.input_ids.copy()

  # because BERT automatically shifts the labels, the labels correspond exactly to `decoder_input_ids`. 
  # We have to make sure that the PAD token is ignored
  batch["labels"] = [[-100 if token == tokenizer.pad_token_id else token for token in labels] for labels in batch["labels"]]

  return batch

# only use 32 training examples for notebook - DELETE LINE FOR FULL TRAINING
# train_data = train_data.select(range(32))

train_data = train_data.map(
    process_data_to_model_inputs, 
    batched=True, 
    batch_size=batch_size,
)
train_data.set_format(
    # type="torch", columns=["input_ids", "attention_mask", "decoder_input_ids", "decoder_attention_mask", "labels"],
    type="torch", columns=["input_ids", "labels"],
)


# only use 16 training examples for notebook - DELETE LINE FOR FULL TRAINING
# val_data = val_data.select(range(16))

val_data = val_data.map(
    process_data_to_model_inputs, 
    batched=True, 
    batch_size=batch_size,
)
val_data.set_format(
    # type="torch", columns=["input_ids", "attention_mask", "decoder_input_ids", "decoder_attention_mask", "labels"],
    type="torch", columns=["input_ids", "labels"],
)

Map:   0%|          | 0/135792 [00:00<?, ? examples/s]

Map:   0%|          | 0/6502 [00:00<?, ? examples/s]

### **Warm-starting the Encoder-Decoder Model**

In [7]:
# from transformers import EncoderDecoderModel
from transformers import BartForConditionalGeneration

bart = BartForConditionalGeneration.from_pretrained('Ayaka/bart-base-cantonese')
# bart = EncoderDecoderModel.from_encoder_decoder_pretrained("Ayaka/bart-base-cantonese", "Ayaka/bart-base-cantonese")

In [9]:
# set special tokens
bart.config.decoder_start_token_id = tokenizer.bos_token_id
bart.config.eos_token_id = tokenizer.eos_token_id
bart.config.pad_token_id = tokenizer.pad_token_id

# sensible parameters for beam search
# bart.config.vocab_size = bart.config.decoder.vocab_size
bart.config.max_length = 128
bart.config.min_length = 3
# bart.config.no_repeat_ngram_size = 3
bart.config.early_stopping = True
# bart.config.length_penalty = 2.0
bart.config.num_beams = 4

### **Fine-Tuning Warm-Started Encoder-Decoder Models**

In [10]:
import sacrebleu

def compute_metrics(pred):
    # print("Start compute_metrics")
    labels_ids = pred.label_ids
    pred_ids = pred.predictions

    # all unnecessary tokens are removed
    pred_str = [s.replace(" ", "") for s in tokenizer.batch_decode(pred_ids, skip_special_tokens=True)]
    print("Predicted:", pred_str)
    labels_ids[labels_ids == -100] = tokenizer.pad_token_id
    label_str = [s.replace(" ", "") for s in tokenizer.batch_decode(labels_ids, skip_special_tokens=True)]
    print("Target:", label_str)

    # bleu_score = bleu.compute(predictions=pred_str, references=label_str, tokenizer=char_tokenizer)["bleu"]
    # chrf_score = chrf.compute(predictions=pred_str, references=label_str)["score"]

    bleu = sacrebleu.BLEU(trg_lang="zh")
    bleu_score = bleu.corpus_score(pred_str, [label_str]).score

    chrf = sacrebleu.CHRF()
    chrf_score = chrf.corpus_score(pred_str, [label_str]).score

    return {
        "bleu": bleu_score,
        "chrf": chrf_score,
    }

In [11]:
# Test CharBLEU
predictions = ['我啲咁耐就攪掂嘞，真係掯', '你幾時得嚟吖']
references = ['我啲咁耐就攪掂嘞，真係掯', '你幾時得嚟吖']

bleu = sacrebleu.BLEU(trg_lang="zh")
bleu_score = bleu.corpus_score(predictions, [references]).score
assert bleu_score - 100 <= 1e-9

Cool! Finally, we start training.

In [13]:
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments

import warnings
warnings.filterwarnings('ignore')

# set training arguments - these params are not really tuned, feel free to change
training_args = Seq2SeqTrainingArguments(
    output_dir="./",
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    predict_with_generate=True,
    use_mps_device=True,
    do_train=True,
    evaluation_strategy="steps",
    do_eval=True,
    logging_steps=200,  # set to 1000 for full training
    save_steps=1000,  # set to 500 for full training
    eval_steps=1000,  # set to 8000 for full training
    warmup_steps=2000,  # set to 2000 for full training
    # max_steps=10, # delete for full training
    overwrite_output_dir=True,
    save_total_limit=8,
    fp16=False,
)

# instantiate trainer
trainer = Seq2SeqTrainer(
    model=bart,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=train_data,
    eval_dataset=val_data.select(range(batch_size * 50)),
)
trainer.train()

  0%|          | 0/12732 [00:00<?, ?it/s]

{'loss': 0.8357, 'learning_rate': 5e-06, 'epoch': 0.05}
{'loss': 0.6021, 'learning_rate': 1e-05, 'epoch': 0.09}
{'loss': 0.216, 'learning_rate': 1.5e-05, 'epoch': 0.14}
{'loss': 0.1557, 'learning_rate': 2e-05, 'epoch': 0.19}
{'loss': 0.1325, 'learning_rate': 2.5e-05, 'epoch': 0.24}


  0%|          | 0/50 [00:00<?, ?it/s]

Predicted: ['這一一一就一這一一一這一就一一就就就一早就就這就就搞就一遲就就遲就一搞就這，這這這就這這一久就這一樣，就這麼這這麼久就一久了一久，這一些那那久就就些那一久久了這久就遲了這些那久久就搞一久一久這些久就久就熬了一些久了就一些這些就一次就一', '我', '爸爸爸他爸爸一眼', '說話好似雞啄般', '我了錢', '使錢錢錢錢畀佢', '錢你', '帽', '有', '！！', '一，，，沒有幾何啫', '他', '他', '你講過的了，是咪先', '讀歪就是普通話嘞', '順？？', '看戲', '我', '我', '我叫你選他做班長', '他', '你你你好叻呀！', '黃黃去', '我我我我搶我我一我我三粒糖', '做課課', '我錢', '張枱抹', '你借五毫你，你連句多謝都沒', '啲衫洗', '你寫字你不要在裏喐喐', '信信媽媽', '敵敵人', '我我我', '我賺咗我五蚊', '我', '還你五，遲還給你，', '伙伙伙還欠伙伙三個月人工', '勸他不要哭！', '逼我做這的事！', '這一你你你這一一一做一一你你一樣做，一一辛辛苦苦苦辛苦的苦苦！你一苦苦你苦苦，你你的苦辛辛一苦，苦苦是苦苦', '嗰啲嘢出嚟', '！！！', '你吃', '筷', '你', '生', '生樣', '八八十八八八點仍未有人嚟', '命命命', '事', '生你', '你一事', '？？？', '都想要', '教', '衫', '', '他', '我教這一科十年', '書', '你你你', '我幫他太搵師傅教車', '一邊唞氣', '啤好', '去不？', '戲', '？', '這', '他個樣幾得敕', '沒玩', '叫？', '你在攪，人們都冇辦法休息', '？？？', '在出便', '？嗎？？？', '他這個人，事零多多', '他', '我不這他，一是有錯怎人原說如下她你話沒嘛明誰那應上姐問無實任何到子差當本也得自現都對', '作，好人都有限，', '呢？', '你', '大仔大仔喇', '買嘢好醃的', '以為那著著', '生他', '醃尖', '痛痛就睇醫醫', '！', '題', '人人，做什都不行，做事都不得', '嘛', '？？？', '人', '啲功做完', '張椅有啲喐', '都來喇，仲傾咩偈呀？', '你好叻', '個你',

  0%|          | 0/50 [00:00<?, ?it/s]

...

  0%|          | 0/50 [00:00<?, ?it/s]

Predicted: ['這些那久就完成了，真膩', '何時得至吖', '他望了他爸爸一眼', '他鬼般生氣，講話好像雞啄不斷這樣', '他騙了我好多錢', '將這些錢給他', '給了三次錢你', '戴了頂紅色的帽子', '的有幾重', '到死！', '有幾何吖，沒有什麼幾何而已', '這個地方得他一個人咋', '他很俊男', '跟你説過的了，是不是先', '廣東話讀歪點就是普通話了', '有什麼順東西嗎？', '看過三次戲', '你借錢我', '他給我三本書', '他逼我叫你選他做班長', '送枝筆他', '你估你很聰明嗎！', '他喊亞黃去', '他強行搶了我三粒糖', '做完這些功課', '我這些錢', '把桌子擦一擦', '我借五蚊你，你連句感謝都無', '把這些衣服洗了', '人家寫字你不要在這裏喐喐貢', '寫封信給媽媽', '與敵人拼命', '持杯茶給我', '那間商店賺了我五蚊', '你借我錢', '我借你五蚊，遲早還是要還給你的', '這個老闆仍欠員工三個月工資', '你就勸一下他不要哭了！', '你別逼我做這樣的東西！', '你這樣的話做法，正一拿苦至辛！', '持嗰些東西出至', '我當他好人添！', '我請你吃飯', '我對筷子', '我教了你十年英文', '長得十分醜怪', '生得真的醜樣', '真沒解八點鐘仍未有人至', '條命凍過水', '無謂攪這麼多東西喇', '長得像你', '麻煩你一件事', '下午開會嗎？', '什麼鬼東西都不想要', '教了幾十年書', '洗了這些衣服', '被他打了一下', '送枝筆給他', '我教了這一科十年', '我本書', '我問你一個問題', '亞郭叫我幫他太太找師傅教車', '一邊唞涼一邊聊天', '這個嬰孩仔好可愛', '你去不去呀？', '這套電影看得啊', '你要不要啊？', '你認為多麼漂亮呢', '你看他的樣子幾得敕', '這個地方沒有什麼好玩', '你叫什麼名字呀？', '你們在這裏搗亂，別人都沒辦法休息了', '你不去嗎？', '他站在外邊', '你躝了去哪裏？', '他這個人鬼五馬六的事零舍多', '他很打得', '他沒錯啊，為什麼説他呢？', '他的作風這麼搞怪，好人都有限了', '那怎麼辦呢？', '他想找你聊聊', '你都大仔喇', '他購物很醃尖的', '你以為那著數咩', 

  0%|          | 0/50 [00:00<?, ?it/s]

Predicted: ['這些那久就完成了，真膩', '何時得至吖', '他望了他爸爸一眼', '他鬼般生氣，講話好像雞啄不斷這樣', '他騙了我好多錢', '將這些錢給他', '我給了三次錢你', '戴了頂紅色的帽子', '的有幾重', '到死！', '有幾何吖，沒有什麼幾何而已', '這個地方得他一個人咋', '他很俊男', '跟你講過的了，是不是先', '廣東話讀歪點就是普通話了', '有什麼順東西嗎？', '看過三次戲', '你借錢我', '他給三本書我', '他逼我叫你選他做班長', '贈送枝筆他', '你估你很聰明嗎！', '他喊亞黃去', '他強行搶了我三粒糖', '做完這些功課', '我這些錢', '把桌子擦一擦', '我借五蚊你，你連句感謝都無', '把這些衣服洗了', '人家寫字你不要在這裏喐喐貢', '寫封信給媽媽', '與敵人拼命', '持杯茶給我', '那間店鋪賺了我五蚊', '你借我錢', '我借你五蚊，遲早還是要還給你的', '這個老闆仍欠員工三個月工資', '你就勸一下他不要哭了！', '你別逼我做這樣的事！', '你這樣的話做法，正一捲苦至辛！', '持嗰些東西出至', '我當他好人添！', '我請你吃飯', '我對筷子', '我教了你十年英文', '長得十分醜怪', '生得真的醜樣', '真沒解八點鐘仍未有人至', '條命凍過水', '無謂攪這麼多事情喇', '長得像你', '我麻煩你一件事', '下午開會嗎？', '什麼鬼東西都不想要', '教了幾十年書', '洗了這些衣服', '被他打了一下', '送枝筆給他', '我教了這一科十年', '我本書', '我問你一個問題', '亞郭叫我幫他太太查師傅教車', '一邊唞涼一邊聊天', '這個嬰孩仔好可愛', '你去不去呀？', '這套電影看得啊', '你要不要啊？', '你認為多麼漂亮呢', '你看他的樣子幾得敕', '這個地方沒有什麼好玩', '你叫什麼名字呀？', '你們在這裏搗亂，人家都沒辦法休息了', '你不去嗎？', '他站在外邊', '你躝了去哪裏？', '他這人鬼五馬六的事零舍多', '他很打得', '他沒錯啊，為什麼説他呢？', '他的作風這麼搞怪，好人都有限了', '那怎麼辦呢？', '他想找你聊聊', '你都大仔喇', '他購物很醃尖的', '你以為那著數咩',

TrainOutput(global_step=12732, training_loss=0.076975904767932, metrics={'train_runtime': 15408.4251, 'train_samples_per_second': 26.439, 'train_steps_per_second': 0.826, 'train_loss': 0.076975904767932, 'epoch': 3.0})

### **Evaluation**

Awesome, we finished training our dummy model. Let's now evaluated the model on the test data. We make use of the dataset's handy `.map()` function to generate a summary of each sample of the test data.

In [15]:
from transformers import BertTokenizer, BartForConditionalGeneration

tokenizer = BertTokenizer.from_pretrained('Ayaka/bart-base-cantonese')
model = BartForConditionalGeneration.from_pretrained("./checkpoint-12000").to('mps')

# only use 16 training examples for notebook - DELETE LINE FOR FULL TRAINING
# test_data = test_data.select(range(16))

batch_size = 64  # change to 64 for full evaluation

pred_file = open("test.pred.man", "w+")

# map data correctly
def generate_summary(batch):
    # Tokenizer will automatically set [BOS] <text> [EOS]
    # cut off at BERT max length 512
    inputs = tokenizer(batch["can"], padding="max_length", truncation=True, max_length=128, return_tensors="pt")
    input_ids = inputs.input_ids.to('mps')
    attention_mask = inputs.attention_mask.to('mps')

    outputs = model.generate(input_ids, attention_mask=attention_mask)

    # all special tokens including will be removed
    output_str = tokenizer.batch_decode(outputs, skip_special_tokens=True)
    batch["pred"] = [s.replace(" ", "") for s in output_str]
    for man, pred in zip(batch["man"], batch["pred"]):
        pred_file.write("P: " + pred + "\n")
        pred_file.write("T: " + man + "\n\n")
    return batch

results = test_data.map(generate_summary, batched=True, batch_size=batch_size)

pred_str = results["pred"]
label_str = results["man"]

# bleu_score = bleu.compute(predictions=pred_str, references=label_str, tokenizer=char_tokenizer)["bleu"]
# chrf_score = chrf.compute(predictions=pred_str, references=label_str)["score"]

bleu = sacrebleu.BLEU(trg_lang="zh")
bleu_score = bleu.corpus_score(label_str, [pred_str]).score
chrf = sacrebleu.CHRF()
chrf_score = chrf.corpus_score(label_str, [pred_str]).score

print("BLEU score:", bleu_score)
print("CHRF score:", chrf_score)


Map:   0%|          | 0/6502 [00:00<?, ? examples/s]

BLEU score: 29.633424907053794
CHRF score: 26.308656364291807
